## **Pre-Flight Planning**

The algorithm 1 finds routes that don't exceed the MAVs maximum flight time and, at the same time, heads back to the home location (the orange helipad). Then, the algorithm 2 schedules the take-off time of the MAVs. The focus of the algorithms is not to minimize the delivery time, but the battery consumption. We only implemented the algorithm 1, which resembles Prim, due to our time limits.

This is part of a research in progress. Another part of this work is in the following repository:

https://github.com/projeto-de-algoritmos/Grafos2_ClosestLandingZone


In [1]:
# Run this cell only once
!git clone https://github.com/projeto-de-algoritmos/Greed_DisasterAidPreFlightPlanning

In [2]:
%cd Greed_DisasterAidPreFlightPlanning

/content/Greed_DisasterAidPreFlightPlanning


In [3]:
import landing_zone_detection
from mock_data.data import RandomAerialImageDataGenerator
from preflight_planning.graph_utils import find_routes, Params
from landing_zone_detection.graph_utils import find_landing_zone
from landing_zone_detection.visualization_utils import *

from IPython.display import clear_output, display
import ipywidgets

In [4]:
# initialize the random data generator
random_data_generator = RandomAerialImageDataGenerator(
    width=224*6,
    height=224*6,
)

In [5]:
slider_speed = ipywidgets.IntSlider(
    value=1, min=1, max=100, step=1  # units per minute
)
slider_landing_time = ipywidgets.IntSlider(
    value=10, min=10, max=5*60, step=5  # seconds
)
slider_takeoff_time = ipywidgets.IntSlider(
    value=10, min=10, max=5*60, step=5  # seconds
)
slider_maximum_flight_time = ipywidgets.IntSlider(
    value=13, min=1, max=90, step=1  # minutes
)
# slider_reload_time = ipywidgets.IntSlider(
#     value=5, min=5, max=10*60, step=5  # seconds
# )
# slider_battery_switching_time = ipywidgets.IntSlider(
#     value=30, min=30, max=10*60, step=10  # seconds
# )
# slider_total_number_of_batteries = ipywidgets.IntSlider(
#     value=4, min=1, max=15, step=1
# )
# slider_num_mav = ipywidgets.IntSlider(
#     value=3, min=1, max=5, step=1
# )
slider_num_people = ipywidgets.IntSlider(
    value=3, min=1, max=20, step=1
)
slider_num_packets = ipywidgets.IntSlider(
    value=2, min=1, max=10, step=1
)

In [6]:
# widgets
update_data_button = ipywidgets.Button(description='UPD DATA')
update_routes_button = ipywidgets.Button(description='UPD ROUTES')

output_map = ipywidgets.Output()
output_map_with_routes = ipywidgets.Output()

In [7]:
params = Params(
    speed=slider_speed.value,
    landing_time=slider_landing_time.value,
    takeoff_time=slider_takeoff_time.value,
    maximum_flight_time=slider_maximum_flight_time.value,
    # reload_time=slider_reload_time.value,
    # battery_switching_time=slider_battery_switching_time.value,
    # total_number_of_batteries=slider_total_number_of_batteries.value,
    # num_mav=slider_num_mav.value,
    num_people=slider_num_people.value,
    num_packets=slider_num_packets.value,
)

def update_params(unuseful_arg):
    global params
    params.speed = slider_speed.value
    params.landing_time = slider_landing_time.value
    params.takeoff_time = slider_takeoff_time.value
    params.maximum_flight_time = slider_maximum_flight_time.value
    # params.reload_time = slider_reload_time.value
    # params.battery_switching_time = slider_battery_switching_time.value
    # params.total_number_of_batteries = slider_total_number_of_batteries.value
    # params.num_mav = slider_num_mav.value
    params.num_people = slider_num_people.value
    params.num_packets = slider_num_packets.value


In [8]:
def update_random_data(unuseful_arg):
    global data
    # Generate random data.
    data = random_data_generator.generate(
        people_quantity=slider_num_people.value
    )
    # Plot the generated map (frame grid).
    with output_map:
        clear_output(True)
        plot_frame(
            data.frame,
            width=data.frame.shape[0],
            height=data.frame.shape[1]
        )

In [9]:
COLOR_OPTIONS = [
    [255,0  ,0  ],  # blue
    # [255,255,0  ],  # turquoise
    [255,0  ,255],  # purple
    [0,  0,  0  ],  # black
    [0  ,255,0  ],  # green
    [0  ,0  ,255],  # red
    [255,255,255],  # white
    [0  ,255,255],  # yellow  
]
tmp_color_options = COLOR_OPTIONS[:]


def update_routes(unuseful_arg):
    # data, params
    global tmp_color_options
    uav_routes, uav_elapsed_times = find_routes(
        person_coord_list=data.person_coord_list.copy(),
        adj_matrix_shape=data.adj_matrix.shape,  # used just for simulation purposes
        home_coord=data.helipad_coord.copy(),
        params=params
    )
    frame_to_plot = data.frame.copy()

    with output_map_with_routes:
        clear_output(True)
        if len(uav_routes[0]) > 1:
            for route in uav_routes:
                if len(tmp_color_options) < 1:
                    tmp_color_options = COLOR_OPTIONS[:]
                color_idx = np.random.choice(len(tmp_color_options))
                color = tmp_color_options[color_idx][:]
                del tmp_color_options[color_idx]
                prev_coord = route[0][:]
                for coord in route[1:]:
                    frame_to_plot = cv2.line(
                        frame_to_plot,
                        (prev_coord[1]*random_data_generator.row_size,
                         prev_coord[0]*random_data_generator.col_size),
                        (coord[1]*random_data_generator.row_size,
                         coord[0]*random_data_generator.col_size),
                         color,
                         5
                    )
                    prev_coord = coord[:]
            plot_frame(
                frame_to_plot,
                width=frame_to_plot.shape[0],
                height=frame_to_plot.shape[1]
            )
        else:
            plot_frame(
                frame_to_plot,
                width=frame_to_plot.shape[0],
                height=frame_to_plot.shape[1]
            )
            print('No route found!')

In [10]:
slider_speed.observe(update_params, names='value')
slider_landing_time.observe(update_params, names='value')
slider_takeoff_time.observe(update_params, names='value')
slider_maximum_flight_time.observe(update_params, names='value')
# slider_reload_time.observe(update_params, names='value')
# slider_battery_switching_time.observe(update_params, names='value')
# slider_total_number_of_batteries.observe(update_params, names='value')
# slider_num_mav.observe(update_params, names='value')
slider_num_people.observe(update_params, names='value')
slider_num_packets.observe(update_params, names='value')

update_data_button.on_click(update_random_data)
update_routes_button.on_click(update_routes)

In [11]:
# initialize the app
update_params(unuseful_arg=None)
update_random_data(unuseful_arg=None)
update_routes(unuseful_arg=None)


## **How to use**

There's a button to generate new random data and another one to update the routes. If you generate new data, please wait for the images to show up before pressing the "update routes" button.


### **MAV Speed** (unit per minute)
How many little squares can the MAV fly per minute.

In [12]:
display(slider_speed)

IntSlider(value=1, min=1)

### **Landing Time** (seconds)
Time each MAV takes to land vertically (we may be not considering other kinds of landing).


In [13]:
display(slider_landing_time)

IntSlider(value=10, max=300, min=10, step=5)

### **Take-Off Time** (seconds)
Time each MAV takes to takeoff vertically (we may be not considering other kinds of takeoff).


In [14]:
display(slider_takeoff_time)

IntSlider(value=10, max=300, min=10, step=5)

### **Maximum Flight Time** (minutes)
Maximum flight time of each MAV. We assume that there's only one type of MAV and that every battery lasts the same amount of time.


In [15]:
display(slider_maximum_flight_time)

IntSlider(value=13, max=90, min=1)

### (TODO) **Battery Switching Time** (seconds)
Time it takes to switch the battery of a MAV when it is turned off. We're not considering recharging the batteries yet.


In [16]:
# display(slider_battery_switching_time)

### (TODO) **Total Number of Batteries**
This is not the number of extra batteries. It is the total number of batteries.


In [17]:
# display(slider_total_number_of_batteries)

### (TODO) **Time to Reload MAV**
Time to give a new packet to the MAV.

In [18]:
# display(slider_reload_time)

### (TODO) **Number of MAVs**

In [19]:
# display(slider_num_mav)

### **Number of People**

In [20]:
display(slider_num_people)

IntSlider(value=3, max=20, min=1)

### **Max Number of Packets per MAV**

In [21]:
display(slider_num_packets)

IntSlider(value=2, max=10, min=1)

### **Update the random image.**


In [22]:
display(update_data_button)

Button(description='UPD DATA', style=ButtonStyle())

### **Update the routes.**


In [23]:
display(update_routes_button)

Button(description='UPD ROUTES', style=ButtonStyle())

### **Random Image**

In [24]:
display(output_map)

Output()

### **Random Image With the Routes of the MAVs**

In [26]:
display(output_map_with_routes)

Output()